In [139]:
import numpy as np
import pandas as pd
from pulp import *
from geopy.distance import distance
import random
import pickle

In [72]:
wells = pd.read_csv("data/wells/AllWells_20210915.csv")
wells_oilgas = wells[wells['WellTypeLa']== 'Oil & Gas']
wells_latlon = wells_oilgas[['Latitude', 'Longitude']].to_records(index=False)
wells_ids = wells_oilgas['API'].tolist()

In [85]:
wells_oilgas.head()

OID        API LeaseName WellNumber WellStatus WellType WellTypeLa  \
53   -1  408300962   Alegria          1    Plugged       OG  Oil & Gas   
54   -1  408300972   Alegria         10    Plugged       OG  Oil & Gas   
55   -1  408300974   Alegria         14    Plugged       OG  Oil & Gas   
56   -1  408300976   Alegria          2    Plugged       OG  Oil & Gas   
57   -1  408300968   Alegria          3    Plugged       OG  Oil & Gas   

   OperatorCo         OperatorNa      FieldName  ... Township Range  \
53      01279  Cal-L Expl. Corp.  Alegria (ABD)  ...      05N   32W   
54      01279  Cal-L Expl. Corp.  Alegria (ABD)  ...      05N   32W   
55      01279  Cal-L Expl. Corp.  Alegria (ABD)  ...      05N   32W   
56      01279  Cal-L Expl. Corp.  Alegria (ABD)  ...      05N   32W   
57      01279  Cal-L Expl. Corp.  Alegria (ABD)  ...      05N   32W   

   BaseMeridi   Latitude   Longitude GISSource isConfiden  isDirectio  \
53         SB  34.471405 -120.271706       hud          N           N   
54         SB  34.469040 -120.257660       hud          N           N   
55         SB  34.474018 -120.254334       hud          N           N   
56         SB  34.472298 -120.271194       hud          N           N   
57         SB  34.469498 -120.264503       hud          N           N   

    SpudDate WellSymbol  
53            PluggedOG  
54            PluggedOG  
55            PluggedOG  
56            PluggedOG  
57            PluggedOG  

[5 rows x 24 columns]

In [23]:
emissions = pd.read_csv(r'./data/Emissions by Unit and Fuel Type - csv/UNIT_DATA-Table 1.csv')
emsCA2019 = emissions[emissions['Reporting Year'] == 2019]
facilities = pd.read_excel(r'./data/ghgp_data_2019.xlsx',
                          sheet_name='Direct Emitters', skiprows=3)
facilities = facilities[facilities.State == 'CA']

In [87]:
facilitiesB = facilities.rename(inplace=False,
                                columns={'Facility Name':'facility_name',
                                         'City':'city',
                                         'Primary NAICS Code':'naics_code',
                                         'Industry Type (subparts)':'industry_subparts',
                                         'Industry Type (sectors)':'industry_sectors'})

emsCA2019loc = pd.merge(emsCA2019, facilitiesB[['Facility Id',
#                                               'Facility Name2',
                                               'city',
                                               'Zip Code',
                                               'Address',
                                               'County',
                                               'Latitude',
                                               'Longitude',
#                                               'Primary NAICS Code2',
                                               'industry_subparts',
                                               'industry_sectors']],
                        how='left', on='Facility Id')
emsCA2019locagg = emsCA2019loc[['Facility Id','Latitude','Longitude','Unit CO2 emissions (non-biogenic)']].dropna().groupby('Facility Id').agg({'Latitude':'min',
                                                           'Longitude':'min',
                                                           'Unit CO2 emissions (non-biogenic)':'sum'})
emsCA2019locagg.reset_index(inplace=True)
emsCA2019locagg = emsCA2019locagg.rename(columns={'Facility Id':'facility_id',
                                                  'Latitude':'lat',
                                                  'Longitude':'lon',
                                                  'Unit CO2 emissions (non-biogenic)':'annual_emissions'})
emsCA2019locagg = emsCA2019locagg[emsCA2019locagg['annual_emissions'] > 0]
emsCA2019locagg.head()


facility_id        lat         lon  annual_emissions
0      1000005  36.923750 -120.104120           60760.1
2      1000051  37.796500 -121.604900           52901.5
3      1000064  35.447778 -119.260000           64051.2
4      1000066  37.074790 -120.877445           69721.9
5      1000070  34.595300 -117.364700         1357906.4

In [84]:
facility_latlon = emsCA2019locagg[['lat', 'lon']].to_records(index=False)
facility_ids = emsCA2019locagg['facility_id'].tolist()

In [102]:
# This cell takes ages to run - it's creating a full cartesian matrix of distances between facilities and wells

distance_matrix = []
for i in facility_latlon:
    distances = []
    for j in wells_latlon:
        dist = distance(i,j).miles
        distances.append(dist)
    distance_matrix.append(distances)

In [94]:
# Generate random numbers for demand volumes, to be changed
well_volumes = [random.uniform(100,1000) for i in wells_ids]

In [103]:
prob = LpProblem('Unbalaced Transportation Problem', LpMinimize)
n_receivers = len(wells_ids)
n_suppliers = len(facility_ids)
supply = emsCA2019locagg['annual_emissions'].tolist()
demand = well_volumes
costs = distance_matrix

In [ ]:
# Takes a long time to run because it's solving the problem
routes = [(i, j) for i in range(n_suppliers) for j in range(n_receivers)]

x = LpVariable.dicts('X', routes, lowBound=0)
prob += lpSum([x[i, j] * costs[i][j] for i in range(n_suppliers) for j in range(n_receivers)])

for i in range(n_suppliers):
    prob += lpSum([x[i, j] for j in range(n_receivers)]) == supply[i]
    
for j in range(n_receivers):
    prob += lpSum([x[i, j] for i in range(n_suppliers)]) <= demand[j]
    
# Solving problem
prob.solve()


In [105]:
# Also takes forever to run

print('Status', LpStatus[prob.status])

print('Z = {}'.format(value(prob.objective)))
for v in prob.variables():
    if (v.varValue > 0):
        print('{} = {}'.format(v.name, v.varValue))

Status Optimal
Z = 5912245318.111822
X_(0,_136084) = 363.79758
X_(0,_136086) = 955.40343
X_(0,_136088) = 818.13738
X_(0,_136090) = 240.09383
X_(0,_136091) = 158.00688
X_(0,_136092) = 507.61208
X_(0,_136093) = 713.27267
X_(0,_136095) = 424.10847
X_(0,_136097) = 277.99646
X_(0,_136099) = 433.44914
X_(0,_136101) = 852.66278
X_(0,_136106) = 884.51993
X_(0,_136107) = 237.23657
X_(0,_136108) = 557.20702
X_(0,_136109) = 403.44382
X_(0,_136112) = 646.59709
X_(0,_136113) = 234.19629
X_(0,_136114) = 634.53243
X_(0,_136115) = 333.57676
X_(0,_136116) = 652.61565
X_(0,_136117) = 133.69395
X_(0,_136118) = 866.56851
X_(0,_136119) = 196.67041
X_(0,_136120) = 797.33213
X_(0,_136121) = 669.63862
X_(0,_136122) = 124.75864
X_(0,_136123) = 353.69293
X_(0,_136124) = 979.89389
X_(0,_136125) = 876.62849
X_(0,_136126) = 776.48752
X_(0,_136127) = 632.61654
X_(0,_136128) = 108.11818
X_(0,_136141) = 395.41373
X_(0,_136142) = 558.73323
X_(0,_136143) = 299.00985
X_(0,_136144) = 550.89054
X_(0,_136149) = 738.29037
X

X_(100,_833) = 924.55415
X_(100,_895) = 353.83194
X_(101,_122656) = 464.9
X_(102,_127681) = 816.79495
X_(102,_127682) = 186.41893
X_(102,_127683) = 427.22764
X_(102,_127684) = 395.99109
X_(102,_127685) = 265.14616
X_(102,_127686) = 218.39404
X_(102,_127687) = 496.03128
X_(102,_127688) = 982.46591
X_(102,_127689) = 707.45145
X_(102,_127690) = 932.27639
X_(102,_127691) = 311.56561
X_(102,_127737) = 882.6866
X_(102,_127739) = 264.23682
X_(102,_127740) = 473.54622
X_(102,_127750) = 413.7202
X_(102,_127751) = 898.16751
X_(102,_127752) = 889.5868
X_(102,_127753) = 159.24816
X_(102,_127848) = 934.07283
X_(102,_127849) = 584.06355
X_(102,_127850) = 726.72245
X_(102,_127851) = 260.67963
X_(102,_127857) = 162.57731
X_(102,_127858) = 423.51383
X_(102,_127859) = 772.42274
X_(102,_127860) = 987.43667
X_(102,_127863) = 939.37847
X_(102,_127864) = 883.29868
X_(102,_127865) = 191.02046
X_(102,_127866) = 788.49995
X_(102,_127868) = 923.13531
X_(102,_127870) = 541.99582
X_(102,_127871) = 932.48564
X_(10

X_(102,_129076) = 528.19133
X_(102,_129077) = 604.44206
X_(102,_129078) = 565.08277
X_(102,_129079) = 577.99088
X_(102,_129080) = 313.74304
X_(102,_129081) = 957.70054
X_(102,_129082) = 666.22013
X_(102,_129083) = 563.52183
X_(102,_129084) = 206.85908
X_(102,_129085) = 446.86784
X_(102,_129086) = 505.01522
X_(102,_129087) = 259.35077
X_(102,_129100) = 315.31591
X_(102,_129106) = 343.87165
X_(102,_129107) = 400.58666
X_(102,_129111) = 432.46634
X_(102,_129114) = 179.42215
X_(102,_129116) = 646.3925
X_(102,_129117) = 451.76006
X_(102,_1489) = 849.1111
X_(102,_153402) = 889.52253
X_(102,_153403) = 765.38228
X_(102,_153404) = 702.04377
X_(102,_153405) = 234.91254
X_(102,_153406) = 411.94998
X_(102,_153407) = 391.63667
X_(102,_153408) = 264.30562
X_(102,_153411) = 451.66476
X_(102,_153412) = 873.68616
X_(102,_153744) = 119.20719
X_(102,_153766) = 917.05903
X_(102,_153767) = 109.62637
X_(102,_153768) = 229.09348
X_(102,_153769) = 743.71919
X_(102,_153770) = 679.4247
X_(102,_153771) = 199.261

X_(102,_80764) = 458.26163
X_(103,_132581) = 488.19
X_(103,_132601) = 797.97886
X_(103,_132602) = 275.57054
X_(103,_132606) = 176.16793
X_(103,_132608) = 101.39277
X_(103,_133314) = 841.18827
X_(103,_136994) = 368.00028
X_(103,_61603) = 468.50925
X_(103,_61609) = 835.87624
X_(103,_69593) = 79.816438
X_(103,_70700) = 762.35897
X_(103,_71557) = 202.46278
X_(103,_71559) = 349.48767
X_(104,_70029) = 815.34707
X_(104,_70059) = 170.53009
X_(104,_70060) = 747.67853
X_(104,_70193) = 269.51905
X_(104,_70198) = 267.46812
X_(104,_70311) = 371.77776
X_(104,_70312) = 650.42349
X_(104,_71660) = 790.21266
X_(104,_71665) = 714.64609
X_(104,_71670) = 475.68859
X_(104,_71681) = 138.78632
X_(104,_71704) = 252.87295
X_(104,_71718) = 613.55553
X_(104,_71765) = 978.82188
X_(104,_71766) = 349.07186
X_(105,_61640) = 140.63912
X_(105,_61644) = 686.36272
X_(105,_61657) = 569.7081
X_(105,_61675) = 330.32457
X_(105,_61688) = 469.67772
X_(105,_61689) = 437.09074
X_(105,_61690) = 507.74436
X_(105,_61691) = 619.8295

X_(110,_136078) = 562.05485
X_(110,_13653) = 810.3515
X_(110,_15273) = 527.649
X_(110,_15358) = 781.95845
X_(110,_15359) = 429.49837
X_(110,_15360) = 798.19046
X_(110,_15362) = 764.04223
X_(110,_15501) = 482.08645
X_(110,_15502) = 951.139
X_(110,_15513) = 171.2313
X_(110,_16234) = 939.82288
X_(110,_16236) = 334.7089
X_(110,_16240) = 985.1679
X_(110,_16378) = 284.68721
X_(110,_16386) = 145.53637
X_(110,_16394) = 305.8774
X_(110,_16567) = 813.54605
X_(110,_18457) = 903.33513
X_(110,_19125) = 638.29098
X_(110,_19132) = 698.75377
X_(110,_19133) = 788.48816
X_(110,_19141) = 530.16017
X_(110,_19336) = 854.76495
X_(110,_19340) = 367.84843
X_(110,_19350) = 265.15025
X_(110,_19351) = 522.73207
X_(110,_19359) = 280.60683
X_(110,_20515) = 780.56582
X_(110,_20527) = 241.69006
X_(110,_20528) = 305.10018
X_(110,_20536) = 874.29258
X_(110,_20537) = 857.51219
X_(110,_20571) = 996.53997
X_(110,_20590) = 927.37109
X_(110,_21038) = 680.45464
X_(110,_21061) = 474.8244
X_(110,_21064) = 648.97983
X_(110,_21

...

X_(80,_148941) = 879.99667
X_(80,_148943) = 736.90195
X_(80,_148945) = 705.1763
X_(80,_148946) = 683.74916
X_(80,_148947) = 439.72414
X_(80,_149072) = 844.71754
X_(80,_149440) = 349.49278
X_(80,_149463) = 409.31179
X_(80,_149467) = 326.87396
X_(80,_149492) = 513.42561
X_(80,_149500) = 913.21212
X_(80,_149501) = 952.55644
X_(80,_149507) = 687.06425
X_(80,_149509) = 773.32187
X_(80,_149520) = 192.94993
X_(80,_149527) = 291.70712
X_(80,_149532) = 827.54311
X_(80,_149535) = 824.68722
X_(80,_149536) = 950.1647
X_(80,_149540) = 179.62047
X_(80,_149541) = 417.1216
X_(80,_149545) = 803.78683
X_(80,_149551) = 425.98761
X_(80,_149555) = 876.11184
X_(80,_149619) = 777.65732
X_(80,_149620) = 747.56088
X_(80,_149621) = 981.20195
X_(80,_149622) = 118.31396
X_(80,_149623) = 894.31408
X_(80,_149629) = 931.1102
X_(80,_149630) = 634.39454
X_(80,_149631) = 527.62278
X_(80,_149642) = 964.20161
X_(80,_150078) = 679.49856
X_(80,_150079) = 839.59021
X_(80,_150217) = 333.55362
X_(80,_150223) = 613.99201
X_(80

X_(83,_723) = 313.88052
X_(83,_80546) = 918.03736
X_(83,_80547) = 621.07548
X_(83,_80549) = 349.48765
X_(83,_80550) = 597.63112
X_(83,_80551) = 808.30743
X_(83,_80552) = 678.02744
X_(83,_80553) = 433.48993
X_(83,_80554) = 609.83913
X_(83,_80555) = 544.18542
X_(83,_80556) = 552.68259
X_(83,_80557) = 928.66687
X_(83,_80558) = 526.53791
X_(83,_80559) = 855.28627
X_(83,_80560) = 938.25682
X_(83,_80561) = 793.45874
X_(83,_80562) = 810.55362
X_(83,_80563) = 779.25196
X_(83,_80564) = 405.09018
X_(83,_80565) = 857.14919
X_(83,_80566) = 645.3446
X_(83,_80567) = 776.8992
X_(83,_80568) = 596.78149
X_(83,_80569) = 594.97809
X_(83,_80570) = 989.31552
X_(83,_80571) = 156.84032
X_(83,_80572) = 203.88391
X_(83,_80573) = 212.08184
X_(83,_80574) = 223.91711
X_(83,_80575) = 918.91461
X_(83,_80576) = 628.47229
X_(83,_80577) = 900.18985
X_(83,_80578) = 831.37516
X_(83,_80579) = 123.1033
X_(83,_80580) = 572.61836
X_(83,_80581) = 201.68566
X_(83,_80582) = 549.35706
X_(83,_80584) = 547.39739
X_(83,_80585) = 2

X_(88,_45607) = 107.66746
X_(88,_45611) = 292.81157
X_(88,_45614) = 852.09693
X_(88,_45618) = 64.225419
X_(88,_45725) = 281.28482
X_(88,_45734) = 579.80198
X_(88,_45738) = 410.76101
X_(88,_45740) = 217.29984
X_(88,_45747) = 242.02507
X_(88,_45748) = 600.93702
X_(88,_45749) = 569.13327
X_(88,_45751) = 462.55036
X_(88,_45754) = 623.3973
X_(88,_45755) = 360.3613
X_(88,_45757) = 945.52459
X_(88,_45759) = 972.23163
X_(88,_45760) = 284.63416
X_(88,_45763) = 285.6562
X_(88,_45768) = 618.3139
X_(88,_45770) = 404.16397
X_(88,_45771) = 833.83493
X_(88,_45777) = 227.20386
X_(88,_45779) = 417.77113
X_(88,_45785) = 856.0067
X_(88,_45791) = 614.01796
X_(88,_45797) = 598.30556
X_(88,_45798) = 229.83534
X_(88,_45799) = 608.8867
X_(88,_45801) = 785.87307
X_(88,_45803) = 739.4543
X_(88,_45806) = 198.56945
X_(88,_45812) = 578.53009
X_(88,_45813) = 500.56493
X_(88,_45816) = 265.46731
X_(88,_45820) = 312.60367
X_(88,_45824) = 797.83282
X_(88,_45827) = 942.94613
X_(88,_45828) = 600.73396
X_(88,_45830) = 282

X_(91,_80693) = 726.08312
X_(91,_80694) = 610.78707
X_(91,_80695) = 743.22707
X_(91,_80696) = 452.85679
X_(91,_80697) = 175.47811
X_(91,_80698) = 380.7162
X_(91,_80699) = 925.78689
X_(91,_80700) = 270.05713
X_(92,_114) = 864.4203
X_(92,_115) = 399.16925
X_(92,_120) = 522.59354
X_(92,_121) = 920.74153
X_(92,_123) = 991.29893
X_(92,_125) = 801.69841
X_(92,_127) = 420.95294
X_(92,_129) = 828.51518
X_(92,_130) = 949.45352
X_(92,_131) = 648.19133
X_(92,_132) = 386.09451
X_(92,_134) = 600.62539
X_(92,_135) = 300.79096
X_(92,_136) = 672.26552
X_(92,_137) = 466.3309
X_(92,_143) = 556.81043
X_(92,_148) = 224.15534
X_(92,_151) = 210.95299
X_(92,_153) = 103.88398
X_(92,_165) = 381.14621
X_(92,_176) = 137.92122
X_(92,_180) = 471.99331
X_(92,_68757) = 689.30873
X_(92,_68758) = 197.88114
X_(92,_68761) = 642.47672
X_(92,_68774) = 471.12519
X_(92,_68775) = 666.95791
X_(92,_68776) = 220.53991
X_(92,_68777) = 181.52677
X_(92,_68778) = 689.81842
X_(92,_68779) = 995.57589
X_(92,_68780) = 896.2034
X_(92,_6

X_(96,_53028) = 396.19563
X_(96,_53032) = 370.69536
X_(96,_53034) = 578.51911
X_(96,_53047) = 298.64968
X_(96,_53048) = 564.85733
X_(96,_53049) = 328.83796
X_(96,_53057) = 821.90351
X_(96,_53058) = 380.4703
X_(96,_53059) = 684.51489
X_(96,_53069) = 15.395325
X_(96,_53076) = 555.06265
X_(96,_53083) = 305.11739
X_(96,_53084) = 801.35109
X_(96,_53124) = 676.7589
X_(96,_54637) = 130.50423
X_(96,_54742) = 224.06878
X_(96,_54755) = 454.92724
X_(96,_54920) = 404.53724
X_(96,_54935) = 562.99497
X_(96,_54937) = 103.72185
X_(96,_54938) = 398.8506
X_(96,_54954) = 384.76574
X_(96,_54966) = 226.39652
X_(96,_54969) = 736.45876
X_(96,_54970) = 149.42735
X_(96,_54974) = 888.18448
X_(96,_54989) = 402.30047
X_(96,_54990) = 988.83265
X_(97,_92956) = 988.12405
X_(97,_93083) = 997.93495
X_(97,_93190) = 388.84563
X_(97,_93191) = 333.42493
X_(97,_93192) = 947.6017
X_(97,_93509) = 259.15386
X_(97,_93538) = 258.72387
X_(97,_94409) = 388.99516
X_(97,_94431) = 724.33938
X_(97,_94432) = 799.40192
X_(97,_94433) = 

In [ ]:
volumes_moved = [i.varValue for i in prob.variables()]


In [112]:
total_volume = 0
for i in range(0, len(volumes_moved)):
    total_volume = total_volume + volumes_moved[i]
print(total_volume)

59638912.490185946


In [123]:
volume_matrix = []
k=0
while k < n_suppliers:
    vols = []
    for i in range(n_receivers):
        j = i + k*n_receivers
        vols.append(volumes_moved[j])
    volume_matrix.append(vols)
    k+=1

In [124]:
print(len(volume_matrix))
print(len(volume_matrix[0]))

289
158064


In [125]:
print(len(distance_matrix))
print(len(distance_matrix[0]))

289
158064


In [137]:
results = []
for i in range(n_suppliers):
    f_loc = facility_latlon[i]
    for j in range(n_receivers):
        vol = volume_matrix[i][j]
        if vol > 0:
            w_loc = wells_latlon[j]
            dist = distance_matrix[i][j]
            r = [f_loc, w_loc, dist, vol]
            results.append(r)
results

[[(36.92375, -120.10412),
  (36.23867035, -120.38221741),
  49.70567148469709,
  363.79758],
 [(36.92375, -120.10412),
  (36.24571609, -120.33669281),
  48.508587563657905,
  955.40343],
 [(36.92375, -120.10412),
  (36.25873947, -120.32772064),
  47.51045700832812,
  818.13738],
 [(36.92375, -120.10412),
  (36.224933, -120.303681),
  49.447437294482434,
  240.09383],
 [(36.92375, -120.10412),
  (36.255945, -120.34494),
  47.95499897549916,
  158.00688],
 [(36.92375, -120.10412),
  (36.25171661, -120.36567688),
  48.56787006080628,
  507.61208],
 [(36.92375, -120.10412),
  (36.2595253, -120.34490967),
  47.71744798291879,
  713.27267],
 [(36.92375, -120.10412),
  (36.24553299, -120.33037567),
  48.428311226772756,
  424.10847],
 [(36.92375, -120.10412),
  (36.25021362, -120.3724823),
  48.78122587485087,
  277.99646],
 [(36.92375, -120.10412),
  (36.23385239, -120.33602905),
  49.28804446193506,
  433.44914],
 [(36.92375, -120.10412),
  (36.24369431, -120.32946014),
  48.53761531715911,

In [145]:
file_name = 'data/results/results_toydata.pkl'
open_file = open(file_name, "wb")
pickle.dump(results, open_file)
open_file.close()

In [147]:
## USE THIS CODE TO IMPORT DATA

file_name = 'data/results/results_toydata.pkl'
open_file = open(file_name, "rb")
loaded_list = pickle.load(open_file)
open_file.close()



IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[(36.92375, -120.10412),
 (35.08056641, -119.36569977),
 133.6440128505818,
 318.74636]